In [ ]:
%load_ext autoreload   
%autoreload 2

from src import *
import dill
import nltk
import os
nltk.download('all')

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


[nltk_data] Downloading collection 'all'
[nltk_data]    | 
[nltk_data]    | Downloading package abc to
[nltk_data]    |     C:\Users\piotr\AppData\Roaming\nltk_data...
[nltk_data]    |   Package abc is already up-to-date!
[nltk_data]    | Downloading package alpino to
[nltk_data]    |     C:\Users\piotr\AppData\Roaming\nltk_data...
[nltk_data]    |   Package alpino is already up-to-date!
[nltk_data]    | Downloading package averaged_perceptron_tagger to
[nltk_data]    |     C:\Users\piotr\AppData\Roaming\nltk_data...
[nltk_data]    |   Package averaged_perceptron_tagger is already up-
[nltk_data]    |       to-date!
[nltk_data]    | Downloading package averaged_perceptron_tagger_eng to
[nltk_data]    |     C:\Users\piotr\AppData\Roaming\nltk_data...
[nltk_data]    |   Package averaged_perceptron_tagger_eng is already
[nltk_data]    |       up-to-date!
[nltk_data]    | Downloading package averaged_perceptron_tagger_ru to
[nltk_data]    |     C:\Users\piotr\AppData\Roaming\nltk_data...
[

True

In [3]:
settings = Settings()

In [ ]:
dump_dict = None
with open(settings.paths.ws_dataset_dump_file, 'rb') as file:
    dump_dict = dill.load(file)

writing_style_feature_extractor: FeatureExtractor = dump_dict['feature_extractor']
writing_style_pca_analysis_results: FeatureExtractor = dump_dict['pca_analysis_results']

In [4]:
dataset = DaigtDataset(settings)
dataset.load()

In [5]:
dataset.clean()

In [6]:
print(f"Text removed while cleaning: {DaigtMetadataAnalysis.get_percentage_of_removed_text(dataset)}%.")

Text removed while cleaning: 6.082373628842047%.


In [7]:
preprocessing_results = DaigtPreprocessing(settings).preprocess(dataset)
preprocessing_results.info()

collection num_of_syllabes num_of_complex_words num_of_sentences  \
0       human        14120380               969221           483109   
1     mistral        10682516              1303925           285320   
2       llama         8816281               892279           291480   
3         gpt         2101934               245191            61009   
4      claude         1130911               140517            35002   
5      falcon         3024208               377543            84006   
6        palm         1081325               109961            42883   
7      cohere          187627                20141             5956   
8         ada          213987                19734             7970   
9     babbage          207042                20278             7496   
10      curie          244567                23981             9658   
11    davinci          878067                88110            32060   

   num_of_words num_of_splits  
0       9813375      10769987  
1       6070966       6778864  
2       5503243       6170227  
3       1219763       1368287  
4        621156        686641  
5       1707344       1908469  
6        678476        771607  
7        116050        128760  
8        139634        153940  
9        133039        146166  
10       157212        174694  
11       557249        618860

In [8]:
metrics_analysis_results = DaigtMetricsAnalysis().analyze(preprocessing_results)

In [9]:
writing_style_feature_extractor.get_feature_names()

['source_name',
 'author_name',
 'collection_name',
 'unique_word_count',
 'average_word_length',
 'average_sentence_length',
 'average_syllables_per_word',
 'flesch_reading_ease',
 'flesch_kincaid_grade_level',
 'gunning_fog_index',
 'yules_characteristic_k',
 'herdans_c',
 'maas',
 'simpsons_index',
 '/',
 '#',
 '-',
 ';',
 '[',
 '(',
 ':',
 '"',
 '*',
 '_',
 "'",
 '!',
 '?',
 ',',
 '.',
 '%',
 ')',
 'his',
 'it',
 'was',
 'our',
 'her',
 'of',
 'the',
 'said',
 'he',
 'their',
 'and',
 'its',
 'she',
 'my',
 'in',
 'you',
 'with',
 'a',
 'as',
 'to',
 'that',
 'is']

In [10]:
pca_analysis = DaigtPCAAnalysis(
    settings=settings,
    writing_style_feature_extractor=writing_style_feature_extractor,
    writing_style_pca_analysis_results=writing_style_pca_analysis_results
)
pca_results = pca_analysis.analyze(metrics_analysis_results)

In [11]:
DaigtPCAVisualization(pca_results).visualize()

In [ ]:
if os.path.exists(settings.paths.daigt_dataset_dump_file):
    os.remove(settings.paths.daigt_dataset_dump_file)
with open(settings.paths.daigt_dataset_dump_file, 'wb') as file:
    dill.dump(
        obj={
            "dataset": dataset,
            "preprocessing_results": preprocessing_results,
            "metrics_analysis_results": metrics_analysis_results,
            "feature_extractor": writing_style_feature_extractor,
            "pca_results": pca_results,
        },  
        file=file
    )